# Generating points

We want to generate points on a sphere, where points will be as closely together while sthill "covering" the sphere. It is obvous this will be achived when in the comlex distances between neighbouring points will be equidistant/ we want wo place them so they are evenly distributed around the sphere. 

That is impossible if any number of points where points don't match the numbber of verteces of of platonic solid (4,6,8,12,20). However we can get close. 

We will look at 2 aproaches a a simulation for the Thomson Problem and a deterministic way using Fibonacci lattices.



## Data representations

We will represent points with a vector of points where a point is a vector in itself/ am matrix of size 50x3

In [1]:
function fibonacci_sphere(N::Integer)
    pts = zeros(Float64, N, 3)
    ϕ = π * (sqrt(5)-1)             # golden angle in radians
    for k in 0:(N-1)
        z = 1.0 - 2.0*(k)/((N))     # from 1 to -1
        r = sqrt( 1 - z*z)          # x2 +y2 = 1 - z2, x2+y2=r2
        θ = ϕ * k  # golden angle increment
        x = r * cos(θ)
        y = r * sin(θ)
        pts[k+1, :] = [x, y, z]
    end
    return pts
end

fibonacci_sphere (generic function with 1 method)

In [2]:
pts=fibonacci_sphere(1000)

1000×3 Matrix{Float64}:
  0.0          0.0         1.0
 -0.046612    -0.0427004   0.998
  0.00781177   0.0890111   0.996
  0.0665511   -0.0868041   0.994
 -0.124308     0.0219884   0.992
  0.119026     0.0757148   0.99
 -0.0400969   -0.149158    0.988
 -0.0768541    0.147978    0.986
  0.167357    -0.0611187   0.984
 -0.174591    -0.0720687   0.982
  0.0843443    0.180239    0.98
  0.0624321   -0.199043    0.978
 -0.188417     0.109192    0.976
  ⋮                       
 -0.160995    -0.146644   -0.976
  0.018829     0.207753   -0.978
  0.120628    -0.158269   -0.98
 -0.185899     0.033429   -0.982
  0.150602     0.0951996  -0.984
 -0.0437461   -0.160905   -0.986
 -0.0707984    0.137272   -0.988
  0.132369    -0.0487686  -0.99
 -0.116824    -0.0478345  -0.992
  0.0466422    0.0989369  -0.994
  0.0264991   -0.0853334  -0.996
 -0.0546029    0.0318515  -0.998

### Thomson Simulation

In [3]:
using LinearAlgebra
function grad(pts)
    n=size(pts, 1)
    F=zeros(Float64, n, 3)
    for i in 1:(n-1)
        p_i = pts[i,:]
        for j in (i+1):n
            p_j = pts[j, :]
            v=p_i-p_j
            d=norm(p_i-p_j)
            F[i,:].+=(2*v/(d^2))
            F[j,:].-=(2*v/(d^2))
        end 
    end
    return F
end

function relax_on_sphere!(pts; steps = 10000, dt=0.005, cooling = 0.999, text=false)
    for step in 1:steps
        F=grad(pts)
        pts.+=dt .* F
        for i in 1:size(pts,1)
            pts[i,:] ./= norm(pts[i,:])
        end
        dt *= cooling
    
        if text && (step % 50 == 0 || step == 1)
            # measure minimal pairwise distance
            md = minimal_pairwise_distance(pts)
            println("it=$step dt=$(round(dt, sigdigits=3)) min-dist=$(round(md, sigdigits=6))")
        end
    end
end

function minimal_pairwise_distance(pts)
    N = size(pts,1)
    md = Inf
    for i in 1:N-1
        for j in i+1:N
            d = norm(pts[i,:] - pts[j,:])
            if d < md
                md = d
            end
        end
    end
    return md
end


minimal_pairwise_distance (generic function with 1 method)

In [4]:
using WGLMakie, ColorTypes

function plot_sphere_with_points_web(pts, edges)
    fig = Figure(size=(800, 800))
    ax = Axis3(fig[1,1], aspect=:data)

    # Sphere mesh
    θ = range(0, 2π, length=80)
    φ = range(0, π, length=40)
    x = [sin(phi)*cos(th) for phi in φ, th in θ]
    y = [sin(phi)*sin(th) for phi in φ, th in θ]
    z = [cos(phi) for phi in φ, th in θ]

    # Make sphere transparent
    surface!(ax, x, y, z, color=RGBA(0.5, 0.7, 1.0, 0.2), transparency=true)

    # Points
    scatter!(ax, pts[:,1], pts[:,2], pts[:,3], color=RGBA(1,0,0,1), markersize=15)

    # Edges
    for (i,j) in edges
        lines!(ax, [pts[i,1], pts[j,1]], [pts[i,2], pts[j,2]], [pts[i,3], pts[j,3]], color=:black, linewidth=2)
    end

    fig
end

fig = plot_sphere_with_points_web(pts, [])


In [5]:
relax_on_sphere!(pts,text=true)

it=1 dt=0.005 min-dist=0.091059
it=50 dt=0.00476 min-dist=0.106783
it=100 dt=0.00452 min-dist=0.107094
it=150 dt=0.0043 min-dist=0.107616
it=200 dt=0.00409 min-dist=0.107291
it=250 dt=0.00389 min-dist=0.106574
it=300 dt=0.0037 min-dist=0.106069
it=350 dt=0.00352 min-dist=0.105878
it=400 dt=0.00335 min-dist=0.105841
it=450 dt=0.00319 min-dist=0.105657
it=500 dt=0.00303 min-dist=0.105515
it=550 dt=0.00288 min-dist=0.105549
it=600 dt=0.00274 min-dist=0.105584
it=650 dt=0.00261 min-dist=0.105477
it=700 dt=0.00248 min-dist=0.105437
it=750 dt=0.00236 min-dist=0.105478
it=800 dt=0.00225 min-dist=0.105609
it=850 dt=0.00214 min-dist=0.105548
it=900 dt=0.00203 min-dist=0.105522
it=950 dt=0.00193 min-dist=0.105664
it=1000 dt=0.00184 min-dist=0.105962
it=1050 dt=0.00175 min-dist=0.106212
it=1100 dt=0.00166 min-dist=0.106202
it=1150 dt=0.00158 min-dist=0.106204
it=1200 dt=0.00151 min-dist=0.106214
it=1250 dt=0.00143 min-dist=0.106231
it=1300 dt=0.00136 min-dist=0.106253
it=1350 dt=0.0013 min-dist=0

In [6]:

fig = plot_sphere_with_points_web(pts, [])